In [ ]:
import cv2 as cv
import numpy as np
import matplotlib.pyplot as plt
import copy
import os

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [ ]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int
  prev_point_missing: bool
  open_ending: bool

In [ ]:
def peeling(img):
  img2 = img
  prev_img = img2
  kernel = np.ones((3,3),np.uint8)
  maxsteps = 100
  while np.max(np.max(img2))>0 and maxsteps>0:
    prev_img = img2
    img2 = cv.morphologyEx(img2, cv.MORPH_ERODE, kernel)
    maxsteps = maxsteps-1
  
  #Centre of mass on the skeletonized image
  M = cv.moments(prev_img)
  cX = int(M["m10"] / M["m00"])
  cY = int(M["m01"] / M["m00"])
  centre = [cX,cY]

  return centre

In [ ]:
def center_mass(img):
  M = cv.moments(img)
  cX = int(M["m10"] / M["m00"])
  cY = int(M["m01"] / M["m00"])
  centre = [cX,cY]

  return centre

In [ ]:
#Listing all the videos in a folder

AvailableVideos = os.listdir('/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/01 Videos')
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_10
BIBF_01_16
BIBF_01_7
BIBF_03_16
BIBF_03_6
aktivin01_2
aktivin01_3
hipox03_2
melanoma_GF01_11
zometa01_4
zometa01_6
zometa02_4
zometa03_3
zometa03_5
zometa06_3


In [ ]:
#Setting up parameters
#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
inp_video_path = '/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/01 Videos/'
out_video_path = '/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/04 Estimated Videos/'
out_text_path = '/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/03 Estimated Paths/'


MaxFrame = 70
movementlimit = 50

MaxTracebackDist = 70
MaxTraceback = 3
TracebackCooldown = 5

Clocksize = [140,25]

TrackedIDs = []

In [ ]:
#Iterating through all the chosen cells

for cell_name in CellTypes:
  print(cell_name)
  #Setting up video writing

  cap = cv.VideoCapture(inp_video_path+cell_name+'.mpeg')
  ret, frame1 = cap.read()
  prvs = cv.cvtColor(frame1,cv.COLOR_BGR2GRAY)
  hsv = np.zeros_like(frame1)
  hsv[...,1] = 255

  #FRAME 2
  picture_number=1
  row=1

  #Video Write object
  frame_width=int(cap.get(3))
  frame_height=int(cap.get(4))

  #out_tresholded = cv.VideoWriter(out_path + 'v_2_0_tresholded.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  #out_opened = cv.VideoWriter(out_path + 'v_2_0_opened.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  #out_centres = cv.VideoWriter(out_video_path + cell_name + '_centres.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  out_movements = cv.VideoWriter(out_video_path + cell_name + '_movements.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  #out_one_movement = cv.VideoWriter(out_video_path + cell_name + '_one_movement.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  #out_marked_cells = cv.VideoWriter(out_video_path + cell_name + '_marked_cells.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))

  #Starting the analysis

  Centres = []
  AllCentres = []
  AllPrevCentres = []
  AllPaths = []
  NewCellID = 0

  FrameCounter = 0
  ret, frame2 = cap.read()

  while(ret and FrameCounter<MaxFrame):
      
      next1 = cv.cvtColor(frame2,cv.COLOR_BGR2GRAY)
      
      H,W = next1.shape
      
      ############ SAJAT
      
      #------------ Preprocessing ------------

      tresh = ((1-(next1 < 150)*(next1>100))*255).astype(np.uint8)  #band cut treshold
      #ret0, tresh = cv.threshold(next1,100,255,cv.THRESH_BINARY)
      
      closing_kernel = np.ones((10,10),np.uint8)
      opening_kernel = np.ones((4,4),np.uint8)
      
      closed = cv.morphologyEx(tresh, cv.MORPH_CLOSE, closing_kernel)
      opened = cv.morphologyEx(closed, cv.MORPH_OPEN, opening_kernel)
      opened = cv.morphologyEx(opened, cv.MORPH_OPEN, opening_kernel)
      
      blurred = cv.medianBlur(opened, 11)
      
      #------------ Black and White labeling ------------

      ret0, labels = cv.connectedComponents(blurred)

      numCells = np.max(np.max(labels));

      if FrameCounter%5==0: print("  Frame "+str(FrameCounter)+"\tnumber of cells:"+str(numCells))

      cells = np.zeros((numCells,H,W))

      most_left_pos = np.zeros(numCells)+W #Setting up for min finding
      most_top_pos = np.zeros(numCells)+H #Setting up for min finding
      most_right_pos = np.zeros(numCells) #Setting up for max finding
      most_bottom_pos = np.zeros(numCells) #Setting up for max finding
      

      for i in range(W):
        for j in range(H):
          element = labels[j,i]
          if element !=0:
            element = element-1
            cells[element,j,i] = 1  #Filling the element-th cell's space with ones
            #print(most_bottom_pos[element])
            if i<most_left_pos[element]:  #Finding the most left pos of a cell
              most_left_pos[element]=i;
            if i>most_right_pos[element]: #Finding the most right pos of a cell
              most_right_pos[element]=i;
            if j<most_top_pos[element]:   #Finding the most top pos of a cell
              most_top_pos[element]=j;
            if j>most_bottom_pos[element]:#Finding the most bottom pos of a cell
              most_bottom_pos[element]=j;


      #------------ Frame on the cells ------------

      invalid_cells = []

      Framed_cells = []
      for element in range(numCells):
        if(((int(most_top_pos[element])-int(most_bottom_pos[element]))*(int(most_left_pos[element])-int(most_right_pos[element])))<10000 and
          ((int(most_top_pos[element])-int(most_bottom_pos[element]))*(int(most_left_pos[element])-int(most_right_pos[element])))>100):
          ()
        else:
          invalid_cells.append(element)
        Framed_cells.append(cells[element, int(most_top_pos[element]):int(most_bottom_pos[element]), int(most_left_pos[element]):int(most_right_pos[element])])
        

      #------------ Center mass instead of Peeling ------------
      
      CentresImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)
      PrevCentres = Centres
      Centres = []
      for element in range(numCells):
        if invalid_cells.count(element)==0:
          #Current_center = peeling(Framed_cells[element])
          Current_center = center_mass(Framed_cells[element])
          Current_center[0] += most_left_pos[element]
          Current_center[1] += most_top_pos[element]
          if Current_center[1]<H-Clocksize[1] and Current_center[0]>Clocksize[0]:
            Centres.append(Current_center)
            CentresImage[
                        max([int(Current_center[1])-5,0]):
                        min([int(Current_center[1])+5,H]),
                        max([int(Current_center[0])-5,0]):
                        min([int(Current_center[0])+5,W])
                        ]=(255,0,255)
      

      #------------ Closest neighbour alignment ------------

      if np.size(PrevCentres) != 0:
        Ncentres = np.zeros_like(PrevCentres)
        for c1 in range(np.shape(PrevCentres)[0]):
          mindist = H*W
          for c2 in range(np.shape(Centres)[0]):
            dist = np.sqrt(np.power(PrevCentres[c1][0]-Centres[c2][0], 2)+np.power(PrevCentres[c1][1]-Centres[c2][1], 2)) 
            if(dist<mindist):
              mindist = dist
              Ncentres[c1] = Centres[c2]
        AllCentres.append(Ncentres)
        AllPrevCentres.append(PrevCentres)

      #------------ Creating paths from pairs ------------  

      if np.size(PrevCentres) != 0:
        #for c in range(np.shape(AllPrevCentres)[0]):
        c = np.shape(AllPrevCentres)[0]-1
        for c2 in range(np.shape(AllCentres[c])[0]):
          if np.shape(AllPrevCentres)[0]>1:
            #defining the irrational cases
            if (np.power(AllCentres[c][c2][0]-AllPrevCentres[c][c2][0],2)+np.power(AllCentres[c][c2][1]-AllPrevCentres[c][c2][1],2))<movementlimit*movementlimit:

    ############ Diploma

              if c == np.shape(AllPrevCentres)[0]-1:
                cellp = cellpoint()
                cellp.frame = FrameCounter
                cellp.posx = int(AllCentres[c][c2][0])
                cellp.posy = int(AllCentres[c][c2][1])

                matchingID = -1
                for c3 in range(np.shape(AllPaths)[0]):
                  if AllPaths[c3].frame == FrameCounter-1 and AllPrevCentres[c][c2][0] == AllPaths[c3].posx and AllPrevCentres[c][c2][1] == AllPaths[c3].posy:
                    matchingID = AllPaths[c3].id

                if matchingID ==-1:
                  cellp.id = NewCellID
                  NewCellID = NewCellID+1
                  cellp.prev_missing_point = True
                else:
                  cellp.id = matchingID
                  cellp.prev_missing_point = False

                AllPaths.append(cellp)

            else:
              #"marking" the irrational outliers with -1
              AllCentres[c][c2][0]=-1
              AllCentres[c][c2][1]=-1

      #------------ Marking open endings ------------ 

      for p1 in AllPaths:
        if p1.frame == FrameCounter-1:
          p1.open_ending = True
          for p2 in AllPaths:
            if p2.frame == FrameCounter:
              if p2.id == p1.id:
                p1.open_ending = False

      #------------ Connecting broken up paths ------------ 

      OneMovementImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)

      for p1 in AllPaths:
        for p2 in AllPaths:
          for Traceback in range(MaxTraceback):
            if p1.frame == FrameCounter-Traceback-1:
              if p2.frame == FrameCounter:
                if p1.id != p2.id and p2.prev_missing_point == True and p1.open_ending == True and np.power(p1.posx-p2.posx,2)+np.power(p1.posy-p2.posy,2)<np.power(MaxTracebackDist-Traceback*TracebackCooldown,2):
                  p2.id = p1.id
                  cv.line(OneMovementImage, tuple([p1.posx,p1.posy]), tuple([p2.posx,p2.posy]), (255,0,255), 5)
                  #print(Traceback)

      #------------ Removing repeated IDs ------------ 

      for p1 in AllPaths:
        for p2 in AllPaths:
          if p1.frame == p2.frame and p1.id == p2.id and (p1.posx !=p2.posx or p1.posy != p2.posy):
            p2.id = NewCellID
            NewCellID = NewCellID+1

      #------------ Showing the marked paths ------------   

      MarkedCellsImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)
      MovementsImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)

      for p1 in AllPaths:
        for p2 in AllPaths:
          if p2.frame-1 == p1.frame:
            if p1.id == p2.id:
              cv.line(MovementsImage, tuple([p1.posx, p1.posy]), tuple([p2.posx, p2.posy]), (0,255,0,),5)

              IDcolor = 0
              for TrID in TrackedIDs:
                IDcolor = IDcolor+1
                if p1.id == TrID and p2.id == TrID:
                  cv.line(MarkedCellsImage, tuple([p1.posx, p1.posy]), tuple([p2.posx, p2.posy]), (0+(IDcolor*37)%255,255,0+(IDcolor*29)%255), 5)

              if p2.frame == FrameCounter:
                cv.line(OneMovementImage, tuple([p1.posx, p1.posy]), tuple([p2.posx, p2.posy]), (0,255,0), 5)


      ############ SAJAT VEGE
      
      #Video write
      #out_opened.write(cv.cvtColor(opened, cv.COLOR_GRAY2BGR))
      #out_tresholded.write(cv.cvtColor(tresh, cv.COLOR_GRAY2BGR))
      
      #out_centres.write(CentresImage)
      #out_one_movement.write(OneMovementImage)
      out_movements.write(MovementsImage)
      #out_marked_cells.write(MarkedCellsImage)

      prvs = next1
      
      picture_number+=1
      
      ret, frame2 = cap.read()
      
      FrameCounter +=1

  cap.release()

  #out_opened.release()
  #out_tresholded.release()
  out_movements.release()
  #out_centres.release()
  #out_one_movement.release()
  #out_marked_cells.release()

  cv.destroyAllWindows()

  #Writing all the paths into a txt file

  if os.path.exists(out_text_path+cell_name+'trajectories.txt'):
    os.remove(out_text_path+cell_name+'trajectories.txt')

  OutTrajectoriesTxt = open(out_text_path+cell_name+'trajectories.txt','w')
  for p in AllPaths:
    OutTrajectoriesTxt.write(str(p.frame)+'\t'+str(p.id)+'\t'+str(p.posx)+'\t'+str(p.posy)+'\n')
  OutTrajectoriesTxt.close()

  print("Trajectories successfully written")
  print()

print("Run finished sucessfully")

BIBF06_10
  Frame 0	number of cells:21
  Frame 5	number of cells:19
  Frame 10	number of cells:19
  Frame 15	number of cells:22
  Frame 20	number of cells:19
  Frame 25	number of cells:23
  Frame 30	number of cells:20
  Frame 35	number of cells:19
  Frame 40	number of cells:18
  Frame 45	number of cells:19
  Frame 50	number of cells:20
  Frame 55	number of cells:18
  Frame 60	number of cells:18
  Frame 65	number of cells:19
Trajectories successfully written

BIBF_01_16
  Frame 0	number of cells:22
  Frame 5	number of cells:28
  Frame 10	number of cells:21
  Frame 15	number of cells:37
  Frame 20	number of cells:22
  Frame 25	number of cells:29
  Frame 30	number of cells:21
  Frame 35	number of cells:33
  Frame 40	number of cells:25
  Frame 45	number of cells:34
  Frame 50	number of cells:22
  Frame 55	number of cells:31
  Frame 60	number of cells:24
  Frame 65	number of cells:35
Trajectories successfully written

BIBF_01_7
  Frame 0	number of cells:29
  Frame 5	number of cells:40
  Fra